In [2]:
import csv
import pandas as pd
import numpy as np
import os
from geopy.distance import geodesic as GD
from datetime import datetime, timedelta
import matplotlib

In [3]:
# Set up the input database
# os.getcwd()
# link_csv = 'Users/USER1/Documents/GitHub/BankingATODetectionModule/streamlit_webapp/dummy_db.csv'
os.chdir('/Users/USER1/Documents/GitHub/BankingATODetectionModule/streamlit_webapp')
db = pd.read_csv('dummy_db.csv',index_col='login_id')
db.head(3)

username           login_time  typing_speed  \
login_id                                                
1         lilidora  2022-06-01 07:24:04       201.449   
2           thaole  2022-06-01 10:00:10        80.167   
3          linhvuu  2022-06-01 19:12:03       192.980   

                        device_name      device_uuid        mac_address  \
login_id                                                                  
1                         Lilis-Air  117416513199556  80:65:7c:e7:9d:8f   
2                     Net-desktop-4  300000000000004  8c:7a:aa:ef:d7:04   
3         Linhs-MacBook-Air-2.local   24291951679256  8c:7a:aa:f2:e5:88   

         device_vendor                  device_model device_ram  \
login_id                                                          
1          Apple, Inc.  macOS-12.5.1-arm64-arm-64bit      16 GB   
2                 Dell                       Dell004        3GB   
3          Apple, Inc.  macOS-12.5.1-arm64-arm-64bit      16 GB   

                    ip_v4  ... is_vpn is_proxy is_tor  is_relay        lat  \
login_id                   ...                                               
1          123.20.144.183  ...      0        0      0         0  10.740240   
2            183.81.124.2  ...      0        0      0         0  10.772197   
3         125.235.208.251  ...      0        0      0         0  10.786197   

                 lon           suburd  district                   city  \
login_id                                                                 
1         106.699547  Phường Tân Hưng    Quận 7  Thành phố Hồ Chí Minh   
2         106.661671        Phường 14   Quận 10  Thành phố Hồ Chí Minh   
3         106.696813    Phường Đa Kao    Quận 1  Thành phố Hồ Chí Minh   

           country  
login_id            
1         Việt Nam  
2         Việt Nam  
3         Việt Nam  

[3 rows x 27 columns]

In [4]:
# convert the data
db = db.astype({"device_uuid":"str"})

In [5]:
db.columns

Index(['username', 'login_time', 'typing_speed', 'device_name', 'device_uuid',
       'mac_address', 'device_vendor', 'device_model', 'device_ram', 'ip_v4',
       'ip_country', 'ip_region', 'ip_city', 'ip_lat', 'ip_lon', 'isp_name',
       'isp_org', 'is_vpn', 'is_proxy', 'is_tor', 'is_relay', 'lat', 'lon',
       'suburd', 'district', 'city', 'country'],
      dtype='object')

In [6]:
fields = ['username', 'login_time', 'typing_speed', 'device_name', 'device_uuid',
       'mac_address', 'device_vendor', 'device_model', 'device_ram', 'ip_v4',
       'ip_country', 'ip_region', 'ip_city', 'ip_lat', 'ip_lon', 'isp_name',
       'isp_org', 'is_vpn', 'is_proxy', 'is_tor', 'is_relay', 'lat', 'lon',
       'suburd', 'district', 'city', 'country']

In [7]:
usecase1 = {'username': 'linhvuu',
 'login_time': '2022-06-01 19:12:03',
 'typing_speed': 178.675,
 'device_name': 'Linhs-MacBook-Air-2.local',
 'device_uuid': '24291951679256',
 'mac_address': '8c:7a:aa:f2:e5:88',
 'device_vendor': 'Apple, Inc.',
 'device_model': 'macOS-12.5.1-arm64-arm-64bit',
 'device_ram': '16 GB',
 'ip_v4': '125.235.208.251',
 'ip_country': 'Vietnam',
 'ip_region': 'Ho Chi Minh',
 'ip_city': 'Ho Chi Minh City',
 'ip_lat': 10.75,
 'ip_lon': 106.666672,
 'isp_name': 'Viettel Corporation',
 'isp_org': 'Viettel Corporation',
 'is_vpn': 0,
 'is_proxy': 0,
 'is_tor': 0,
 'is_relay': 0,
 'lat': 10.78619741,
 'lon': 106.6968128,
 'suburd': 'Phường Đa Kao',
 'district': 'Quận 1',
 'city': 'Thành phố Hồ Chí Minh',
 'country': 'Việt Nam'}

In [8]:
usecase3 = db.to_dict(orient='records')[0]
usecase2 = db.to_dict(orient='records')[1]
print(usecase3['username'])
print(usecase2['username'])

lilidora
thaole


In [9]:
# lookup weight
# total score = 100
device_max = 40
ip_max = 30
location_max = 30
wt = {'H':1,'MH':0.75,'M':0.5,'L':0.1}
w_item = {
    'device_uuid': 'H',
    'mac_address': 'H',
    'device_name': 'MH',   
    'device_model': 'M',
    'device_vendor': 'L',

    'ip_v4': 'H',
    'isp_name': 'M',
    'ip_country': 'L',

    'suburd': 'H',
    'district': 'MH',
    'city': 'M',
    'country': 'L'}
    
weight = {}
for i in w_item.keys():
    if i in [ 'ip_country', 'isp_name','ip_v4']:
        weight[i] = wt[w_item[i]] * ip_max
    elif i in ['country','city', 'district','suburd']:
        weight[i] = wt[w_item[i]] * location_max
    else:
        weight[i] = wt[w_item[i]] * device_max
print(weight)

{'device_uuid': 40, 'mac_address': 40, 'device_name': 30.0, 'device_model': 20.0, 'device_vendor': 4.0, 'ip_v4': 30, 'isp_name': 15.0, 'ip_country': 3.0, 'suburd': 30, 'district': 22.5, 'city': 15.0, 'country': 3.0}


In [10]:
weight['device_uuid']

40

In [11]:
#1.2 to get the weight of each value
match = 'device_uuid'
weight[match]

40

In [53]:
# 1.1 to check match for each group 
user = usecase1
location_fields = [ 'country','city', 'district','suburd']
input_u =  {'suburd': 'Phường 5',
    'district': 'Quận 999',
    'city': 'Thành phố Hồ Chí Minh',
    'country': 'Việt Nam'}
user_db = db[db.username==user['username']]
def check_match_per(user,user_db,check = 'loacation'):
    """
    input the check is one of 'location','device','ip'
    """
    match_value = ''
    per = 0
    total_txn = len(user_db)
    if check == 'location':
        fields_check = ['country','city', 'district','suburd']
    elif check == 'device':
        fields_check = ['device_vendor','device_model','device_name','mac_address','device_uuid']
    else:
        fields_check = [ 'ip_country', 'isp_name','ip_v4',]  
    for i in fields_check:
        count =  len(user_db[user_db[i] == user[i]])
        if count > 0:
        # if  user[i] in user_db[i].values and user[i] != '':
            match_value = i
            per = count/total_txn

        elif i == 'mac_address':
            continue
        else:
            break
    # print(f'Match value is {match_value}')
    final_per = get_right_per(user_dict,user_db,match_value,per)
    return match_value,final_per

check_match_per(user,user_db,check='device')

range is from 44.0 to 55


('device_uuid', 1)

In [52]:
get_right_per(user_dict,user_db,match_value,per)

NameError: name 'match_value' is not defined

In [51]:
# to get per of the highest points
# get all the values with count in range ~20% less than the highest
def get_right_per(user_dict,user_db,match_value,per):
    range_highest = 0.2
    count_all = user_db.groupby(match_value).count().login_time
    up = count_all.max()
    down = up*(1-range_highest)
    print(f'range is from {down} to {up}')
    if count_all[user_dict[match_value]] >= down and count_all[user_dict[match_value]] <= up:
        return 1
    else:
        return per

In [13]:
# 2.1 Get velocity of all transactions
def get_vel_all(row):
    # print(row)
    dist = 0
    coor = (row['lat'],row['lon'])
    coor_pre = (row['pre_lat'],row['pre_lon'])
    interval = ''
    vel = ''
    if coor_pre != (0,0):
        dist = GD(coor,coor_pre).km
        interval = (row['login_time'] - row['pre_time']).total_seconds()/(60*60)
        # interval = (row['login_time'] - row['pre_time']).days
        vel = dist/interval
    return vel

In [14]:
#  2. Def to check score_jumping: velocity (H: 600+, M: 80 - 600, S: 40<80) and frequency_jumping (rare or ussually)
user_db.login_time =  pd.to_datetime(user_db.login_time)
user_db['pre_lat'] = user_db['lat'].shift(periods=1, fill_value=0)
user_db['pre_lon'] = user_db['lon'].shift(periods=1, fill_value=0)
user_db['pre_time'] = user_db['login_time'].shift(periods=1,fill_value=0)
user_db['vel'] = user_db.apply(lambda x: get_vel_all(x),axis=1)

/var/folders/l8/r1y7_13x2mq324h61cc4gk4r0000gp/T/ipykernel_70337/224041067.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  user_db.login_time =  pd.to_datetime(user_db.login_time)
/var/folders/l8/r1y7_13x2mq324h61cc4gk4r0000gp/T/ipykernel_70337/224041067.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  user_db['pre_lat'] = user_db['lat'].shift(periods=1, fill_value=0)
/var/folders/l8/r1y7_13x2mq324h61cc4gk4r0000gp/T/ipykernel_70337/224041067.py:4: SettingWithCopyWarning: 
A value is trying to be set 

In [15]:
# 2.2 get vel of the latest txn
user

def get_vel_txn(usecase,user_db):
    """
    get the velocity of the new transaction in usecase and the latest transaction in user's history
    """
    dist = 0
    interval = ''
    latest_txn = user_db.iloc[[-1]]
    coor_txn = (usecase['lat'],usecase['lon'])
    coor_latest = (float(latest_txn['lat']),float(latest_txn['lon']))
    dist = GD(coor_txn,coor_latest).km

    time_txn = datetime.strptime(user['login_time'],'%Y-%m-%d %H:%M:%S')
    interval = (time_txn - latest_txn['login_time'].to_list()[0]).total_seconds()/(60*60)
    try: 
        vel = dist/interval
    except:
        vel = 0
    return(vel)
    # print(vel)

get_vel_txn(user,user_db)

-0.003112011442430221

In [17]:
user

{'username': 'linhvuu',
 'login_time': '2022-06-01 19:12:03',
 'typing_speed': 178.675,
 'device_name': 'Linhs-MacBook-Air-2.local',
 'device_uuid': '24291951679256',
 'mac_address': '8c:7a:aa:f2:e5:88',
 'device_vendor': 'Apple, Inc.',
 'device_model': 'macOS-12.5.1-arm64-arm-64bit',
 'device_ram': '16 GB',
 'ip_v4': '125.235.208.251',
 'ip_country': 'Vietnam',
 'ip_region': 'Ho Chi Minh',
 'ip_city': 'Ho Chi Minh City',
 'ip_lat': 10.75,
 'ip_lon': 106.666672,
 'isp_name': 'Viettel Corporation',
 'isp_org': 'Viettel Corporation',
 'is_vpn': 0,
 'is_proxy': 0,
 'is_tor': 0,
 'is_relay': 0,
 'lat': 10.78619741,
 'lon': 106.6968128,
 'suburd': 'Phường Đa Kao',
 'district': 'Quận 1',
 'city': 'Thành phố Hồ Chí Minh',
 'country': 'Việt Nam'}

In [20]:
user_dict= user

In [21]:
# 2 to get score will be reduced because of jumping
def get_score_jump (user_dict,user_db):
    threshold_vel = {
        'H':600,
        'M':80,
        'L':40,
        'frequency':0.1
    }
    weight_vel = {
        'H':20,
        'M':10,
        "L":5
    }
    many_vel = {
        'Y':0.1,
        'N':1
    }

    # to get how many jumping - low or not
    count_jump = len(user_db[user_db.apply(lambda x: float(x.vel) > threshold_vel['L'] if x.vel != "" else False,axis=1)])

    if count_jump > len(user_db)*threshold_vel['frequency']:
        many_jump = 'Y'
    else:
        many_jump = 'N'

    vel_txn = float(get_vel_txn(user_dict,user_db))


    if vel_txn > threshold_vel['H']:
        score_jump = many_vel[many_jump] * weight_vel['H']
    elif vel_txn > threshold_vel['M']:
        score_jump = many_vel[many_jump] * weight_vel['M']
    elif vel_txn > threshold_vel['L']:
        score_jump = many_vel[many_jump] * weight_vel['L']
    else:
        score_jump = 0

    return(score_jump)


In [23]:
get_score_jump (user_dict,user_db)

0

In [36]:
# 3.1 check vpn (new IP + vpn)


def get_vpn_score (user_dict,user_db):
    vpn_fields =  ['is_vpn',
    'is_proxy',
    'is_tor',
    'is_relay']
    weight_vpn = 10
    vpn_count = 0
    for i in vpn_fields:
        vpn_count += user[i]
    if check_match_per(user_dict,user_db,check = 'ip')[0] != 'ip_v4' and vpn_count > 0:
        return weight_vpn
    else:
        return 0

get_vpn_score(user,user_db)


Match value is ip_v4


0

In [68]:
# 3.2 Check typing speed (IQR)
weight_typing = 10
def check_typing_speed (user,user_db):
    Q1 = np.percentile(user_db.typing_speed,25)
    Q3 = np.percentile(user_db.typing_speed,75)
    IQR = Q3-Q1
    # print(IQR)
    ll = Q1 - 1.5*IQR
    ul = Q3 + 1.5*IQR
    if user['typing_speed'] < ll or user['typing_speed'] > ul:
        return weight_typing
    else:
        return 0

typing_score = check_typing_speed(user,user_db)
# typing_score = check_typing_speed(test,user_db)
typing_score

0

In [69]:
# 4. Def to get_score:
# => The score = score_device * per_app + score_ip * per_app + score_location * per_app (- score_jumping - typing_speed - vpn_check: new + vpn)
user

{'username': 'linhvuu',
 'login_time': '2022-06-01 19:12:03',
 'typing_speed': 178.675,
 'device_name': 'Linhs-MacBook-Air-2.local',
 'device_uuid': '24291951679256',
 'mac_address': '8c:7a:aa:f2:e5:88',
 'device_vendor': 'Apple, Inc.',
 'device_model': 'macOS-12.5.1-arm64-arm-64bit',
 'device_ram': '16 GB',
 'ip_v4': '125.235.208.251',
 'ip_country': 'Vietnam',
 'ip_region': 'Ho Chi Minh',
 'ip_city': 'Ho Chi Minh City',
 'ip_lat': 10.75,
 'ip_lon': 106.666672,
 'isp_name': 'Viettel Corporation',
 'isp_org': 'Viettel Corporation',
 'is_vpn': 0,
 'is_proxy': 0,
 'is_tor': 0,
 'is_relay': 0,
 'lat': 10.78619741,
 'lon': 106.6968128,
 'suburd': 'Phường Đa Kao',
 'district': 'Quận 1',
 'city': 'Thành phố Hồ Chí Minh',
 'country': 'Việt Nam'}

In [70]:
user_db.head(3)

username           login_time  typing_speed  \
login_id                                               
3         linhvuu  2022-06-01 19:12:03       192.980   
7         linhvuu  2022-06-03 01:21:01       133.234   
10        linhvuu  2022-06-04 17:04:16       170.171   

                        device_name       device_uuid        mac_address  \
login_id                                                                   
3         Linhs-MacBook-Air-2.local    24291951679256  8c:7a:aa:f2:e5:88   
7                     Linhs-Samsung  1000000000000002  8c:7a:aa:f2:e5:02   
10        Linhs-MacBook-Air-2.local    24291951679256  8c:7a:aa:f2:e5:88   

         device_vendor                  device_model device_ram  \
login_id                                                          
3          Apple, Inc.  macOS-12.5.1-arm64-arm-64bit      16 GB   
7              Samsung                    Samsung001        2GB   
10         Apple, Inc.  macOS-12.5.1-arm64-arm-64bit      16 GB   

                    ip_v4  ... is_vpn is_proxy is_tor  is_relay        lat  \
login_id                   ...                                               
3         125.235.208.251  ...      0        0      0         0  10.786197   
7           18.162.78.188  ...      1        0      0         0  10.737127   
10          27.65.195.158  ...      0        0      0         0  10.737217   

                 lon         suburd  district                   city   country  
login_id                                                                        
3         106.696813  Phường Đa Kao    Quận 1  Thành phố Hồ Chí Minh  Việt Nam  
7         106.660850       Phường 5    Quận 8  Thành phố Hồ Chí Minh  Việt Nam  
10        106.661484       Phường 5    Quận 8  Thành phố Hồ Chí Minh  Việt Nam  

[3 rows x 27 columns]

In [94]:
user = {'username': 'lilidora',
 'login_time': '2022-06-01 07:24:04',
 'typing_speed': 201.449,
 'device_name': 'Lilkjkis-Air',
 'device_uuid': '11741651319fdsf9556',
 'mac_address': '80:65:7csdfds:e7:9d:8f',
 'device_vendor': 'Apple, Inc.',
 'device_model': 'macOS-12.5.1-arm64-arm-64bit',
 'device_ram': '16 GB',
 'ip_v4': '123.20.fsdf44.183',
 'ip_country': 'Vietnam',
 'ip_region': 'Ho Chi Minh',
 'ip_city': 'Ho Chi Minh City',
 'ip_lat': 10.8326,
 'ip_lon': 106.6581,
 'isp_name': 'VietNam Post and Telecom Corporation',
 'isp_org': '0',
 'is_vpn': 0,
 'is_proxy': 0,
 'is_tor': 0,
 'is_relay': 0,
 'lat': 10.74024034,
 'lon': 106.6995472,
 'suburd': 'Phườngdfs Tân Hưng',
 'district': 'Quận 7',
 'city': 'Thành phố Hồ Chí Minh',
 'country': 'Việt Nam'}

In [95]:
# user = usecase3
user_db = db[db.username == user['username']]

# 4.Get score
def get_risk_score (user_dict,user_db):
    weight = {'device_uuid': 40, 'mac_address': 40, 'device_name': 30.0, 'device_model': 20.0, \
						'device_vendor': 4.0, 'ip_v4': 30, 'isp_name': 15.0, 'ip_country': 3.0, 'suburb': 30, 'district': 22.5, \
							'city': 15.0, 'country': 3.0}
    # check device
    device_match,device_per = check_match_per(user_dict,user_db,check='device')
    device_score = weight[device_match] * device_per

    # check ip
    ip_match,ip_per = check_match_per(user_dict,user_db,check='ip')
    ip_score = weight[ip_match] * ip_per


    # check location
    location_match,location_per = check_match_per(user_dict,user_db,check='location')
    location_score = weight[location_match] * location_per
    return device_score+ip_score+location_score


    print(f'total {device_score+ip_score+location_score}')

lilidora
device_model 12.0
0.6
device_model
isp_name 12.75
district 11.25
total 36.0


In [30]:
user_db.groupby('device_uuid').count().login_time

device_uuid
1000000000000002    45
24291951679256      55
Name: login_time, dtype: int64

In [32]:
db[db.username=='linhvuu'].groupby('device_uuid').count().login_time

device_uuid
1000000000000002    45
24291951679256      55
Name: login_time, dtype: int64

In [33]:
db[db.username=='thaole'].groupby('device_uuid').count().login_time

device_uuid
121577554615100    60
300000000000003    25
300000000000004    15
Name: login_time, dtype: int64

In [34]:
db[db.username=='lilidora'].groupby('device_uuid').count().login_time
# highest and 105

device_uuid
117416513199556    60
20000000000002     40
Name: login_time, dtype: int64

In [48]:
user_dist = user

In [49]:
count_all[user_dist['device_uuid']]

55